# Sound

In [ ]:
#| default_exp core

In [ ]:
#| export
import librosa
import plotly.express as px
from torch_snippets import logger, show, np, pd
from IPython.display import Audio
import soundfile as sf
from fastcore.dispatch import patch_to

In [ ]:
#| export
class Sound:
    def __init__(self, audio, Fs):
        self.audio, self.Fs = audio, Fs

    @classmethod
    def from_path(cls, path):
        audio, Fs = librosa.load(path)
        return cls(audio, Fs)

    def plot(self, slice=None):
        factor = 1 + (int(self.size) // 2)
        audio = self.audio if not slice else self.__getitem__(slice).audio
        Fs = self.Fs
        o = audio[::factor]
        o = pd.DataFrame({'y': o, 'x': np.arange(0, len(audio)/Fs, step=(len(audio)/Fs)/len(o))})
        fig = px.line(o, x='x', y='y')
        show(fig)
        
    def __len__(self):
        return len(self.audio)
    
    def __getitem__(self, item):
        if isinstance(item, slice):
            to, end, step = item.start or 0, item.stop or len(self), item.step or 1
            if step > 0:
                return Sound(self.audio[int(to*self.Fs):int(end*self.Fs):item.step], self.Fs)
            else:
                return Sound(self.audio[int(end*self.Fs):int(to*self.Fs):item.step], self.Fs)
        else:
            return self.audio[item]

    def play(self, x=1):
        logger.info(self.formatted_size[-1])
        assert isinstance(x, int)
        show(Audio(self.audio[::x], rate=self.Fs))

    def write(self, fpath):
        logger.info(f'Writing audiofile of {self.formatted_size[-1]} to {fpath}')
        sf.write(fpath, self.audio, self.Fs, subtype='PCM_24')
        
    def assert_same_sampling_freq(self, other):
        if self.Fs != other.Fs:
            raise NotImplementedError("Yet to implement addition for different freq signals")
        
    def __mul__(self, other):
        self.assert_same_sampling_freq(other)
        return Sound(self.audio + other.audio, self.Fs)

    def __sub__(self, other):
        self.assert_same_sampling_freq(other)
        return Sound(self.audio - other.audio, self.Fs)
    
    def __add__(self, other):
        self.assert_same_sampling_freq(other)
        return Sound(np.r_[self.audio, other.audio], self.Fs)

    
    @property
    def size(self):
        # number of seconds
        return len(self) / self.Fs
        
    @property
    def formatted_size(self):
        _len = self.size; unit = 'seconds'; precision = 3
        if _len > 60: _len = _len / 60; unit = 'minutes'; precision = 2
        if _len > 60: _len = _len / 60; unit = 'hours'; precision = 2
        return _len, unit, precision, f'{_len:.{precision}f} {unit}'

In [ ]:
#| export
@patch_to(Sound, cls_method=True)
def sine(cls, freq, time=1, sampling_freq=22050):
    𝜔 = 2*np.pi*freq
    return cls(np.sin(np.arange(0, time, step=1/sampling_freq)*𝜔), sampling_freq)

    
@patch_to(Sound, cls_method=True)
def blank(cls):
    return cls.sine(0, 0)

In [ ]:
x = Sound.sine(100, 1)
x.play()

[11/11/22 18:55:05] INFO     1.000 seconds                                                     ]8;id=732603;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/142370208.py\142370208.py]8;;\:]8;id=681657;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/142370208.py#play:41\play:41]8;;\

In [ ]:
m, M, s = 30, 60, 1.5
_s = 5
x = Sound.blank()
for y in np.arange(m, M, _s):
    x = x + Sound.sine(y, s)
    
for y in np.arange(M, m, -_s):
    x = x + Sound.sine(y, s)
    
x.play()

[11/11/22 18:55:07] INFO     18.000 seconds                                                    ]8;id=543297;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/142370208.py\142370208.py]8;;\:]8;id=400203;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/142370208.py#play:41\play:41]8;;\

In [ ]:
x = (Sound.sine(100, 5) * Sound.sine(105, 5))
x.play()

[11/11/22 18:55:08] INFO     5.000 seconds                                                     ]8;id=53689;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/142370208.py\142370208.py]8;;\:]8;id=472063;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/142370208.py#play:41\play:41]8;;\

In [ ]:
x[1.5:2.5].plot()

In [ ]:
base = 60
saregama = [1,9/8,5/4,4/3,3/2,5/3,15/8,2]

fs = [f*base for f in saregama]
x = Sound.blank()
for y in fs:
    x = x + Sound.sine(y, 1)

for step in [1,2,3,4,5,10,20,30,50,100]:
    (x[::step] + x[::-step]).play()

[11/11/22 18:49:21] INFO     16.000 seconds                                                   ]8;id=265604;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=952534;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     8.000 seconds                                                    ]8;id=566316;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=998274;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     5.333 seconds                                                    ]8;id=369444;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=770194;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     4.000 seconds                                                    ]8;id=757408;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=900831;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     3.200 seconds                                                    ]8;id=669767;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=673795;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     1.600 seconds                                                    ]8;id=739100;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=546933;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     0.800 seconds                                                    ]8;id=143012;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=132937;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     0.533 seconds                                                    ]8;id=352030;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=211317;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     0.320 seconds                                                    ]8;id=325497;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=358087;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

                    INFO     0.160 seconds                                                    ]8;id=762454;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py\1488321391.py]8;;\:]8;id=6573;file:///var/folders/cp/1fbgq2n922j8ztdsq6551vldkr5sdy/T/ipykernel_51165/1488321391.py#play:41\play:41]8;;\

In [ ]:
x = Sound.from_path('../data/1-1.mp3')